<p style="text-align:center">
    <a href="https://skills.network" target="_blank">
    <img src="https://cf-courses-data.s3.us.cloud-object-storage.appdomain.cloud/assets/logos/SN_web_lightmode.png" width="200" alt="Skills Network Logo"  />
    </a>
</p>


# **Lab: Custom Training Loops in Keras**


Estimated time needed: **30** minutes


In this lab, you will learn to implement a basic custom training loop in Keras. 


## Objectives

By the end of this lab, you will: 

- Set up the environment 

- Define the neural network model 

- Define the Loss Function and Optimizer 

- Implement the custom training loop 

- Enhance the custom training loop by adding an accuracy metric to monitor model performance 

- Implement a custom callback to log additional metrics and information during training


----


## Step-by-Step Instructions:


### Exercise 1: Basic custom training loop: 

#### 1. Set Up the Environment:

- Import necessary libraries. 

- Load and preprocess the MNIST dataset. 


In [ ]:
!pip install tensorflow numpy

In [ ]:
import os
import warnings
import tensorflow as tf 
from tensorflow.keras.models import Sequential, Model
from tensorflow.keras.layers import Dense, Flatten, Input
from tensorflow.keras.callbacks import Callback
import numpy as np

# Suppress all Python warnings
warnings.filterwarnings('ignore')

# Set TensorFlow log level to suppress warnings and info messages
os.environ['TF_CPP_MIN_LOG_LEVEL'] = '2'

# Step 1: Set Up the Environment
(x_train, y_train), (x_test, y_test) = tf.keras.datasets.mnist.load_data() 
x_train, x_test = x_train / 255.0, x_test / 255.0 
train_dataset = tf.data.Dataset.from_tensor_slices((x_train, y_train)).batch(32)


#### 2. Define the model: 

Create a simple neural network model with a Flatten layer followed by two Dense layers. 


In [ ]:
# Step 2: Define the Model

model = Sequential([
    Flatten(input_shape=(28, 28)),
    Dense(128, activation='relu'),
    Dense(10)
])


#### 3. Define Loss Function and Optimizer: 

- Use Sparse Categorical Crossentropy for the loss function. 
- Use the Adam optimizer. 


In [ ]:
# Step 3: Define Loss Function and Optimizer

loss_fn = tf.keras.losses.SparseCategoricalCrossentropy(from_logits=True) 
optimizer = tf.keras.optimizers.Adam()


#### 4. Implement the Custom Training Loop: 

- Iterate over the dataset for a specified number of epochs. 
- Compute the loss and apply gradients to update the model's weights. 


In [ ]:
# Step 4: Implement the Custom Training Loop

epochs = 2
# train_dataset = train_dataset.repeat(epochs)
train_dataset = tf.data.Dataset.from_tensor_slices((x_train, y_train)).batch(32)
for epoch in range(epochs):
    print(f'Start of epoch {epoch + 1}')

    for step, (x_batch_train, y_batch_train) in enumerate(train_dataset):
        with tf.GradientTape() as tape:
            logits = model(x_batch_train, training=True)  # Forward pass
            loss_value = loss_fn(y_batch_train, logits)  # Compute loss

        # Compute gradients and update weights
        grads = tape.gradient(loss_value, model.trainable_weights)
        optimizer.apply_gradients(zip(grads, model.trainable_weights))

        # Logging the loss every 200 steps
        if step % 200 == 0:
            print(f'Epoch {epoch + 1} Step {step}: Loss = {loss_value.numpy()}')


### Exercise 2: Adding Accuracy Metric:

Enhance the custom training loop by adding an accuracy metric to monitor model performance. 

#### 1. Set Up the Environment: 

Follow the setup from Exercise 1. 


In [1]:
import tensorflow as tf 
from tensorflow.keras.models import Sequential 
from tensorflow.keras.layers import Dense, Flatten 

# Step 1: Set Up the Environment
(x_train, y_train), (x_test, y_test) = tf.keras.datasets.mnist.load_data()

# Normalize the pixel values to be between 0 and 1
x_train, x_test = x_train / 255.0, x_test / 255.0 

# Create a batched dataset for training
train_dataset = tf.data.Dataset.from_tensor_slices((x_train, y_train)).batch(32)


#### 2. Define the Model: 
Use the same model as in Exercise 1. 


In [14]:
# Step 2: Define the Model

Model = Sequential([ 
    Flatten(input_shape=(28, 28)),  # Flatten the input to a 1D vector
    Dense(128, activation='relu'),  # First hidden layer with 128 neurons and ReLU activation
    Dense(10)  # Output layer with 10 neurons for the 10 classes (digits 0-9)
])


/Users/govindswarooprahangdale/tfenv/lib/python3.10/site-packages/keras/src/layers/reshaping/flatten.py:37: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(**kwargs)


#### 3. Define the loss function, optimizer, and metric: 

- Use Sparse Categorical Crossentropy for the loss function and Adam optimizer. 

- Add Sparse Categorical Accuracy as a metric. 


In [3]:
# Step 3: Define Loss Function, Optimizer, and Metric

loss_fn = tf.keras.losses.SparseCategoricalCrossentropy(from_logits=True)  # Loss function for multi-class classification
optimizer = tf.keras.optimizers.Adam()  # Adam optimizer for efficient training
accuracy_metric = tf.keras.metrics.SparseCategoricalAccuracy()  # Metric to track accuracy during training


#### 4. Implement the custom training loop with accuracy: 

Track the accuracy during training and print it at regular intervals. 


In [4]:
# Step 4: Implement the Custom Training Loop with Accuracy

epochs = 5  # Number of epochs for training

for epoch in range(epochs):
    print(f'Start of epoch {epoch + 1}')
    
    for step, (x_batch_train, y_batch_train) in enumerate(train_dataset):
        with tf.GradientTape() as tape:
            # Forward pass: Compute predictions
            logits = model(x_batch_train, training=True)
            # Compute loss
            loss_value = loss_fn(y_batch_train, logits)
        
        # Compute gradients
        grads = tape.gradient(loss_value, model.trainable_weights)
        # Apply gradients to update model weights
        optimizer.apply_gradients(zip(grads, model.trainable_weights))
        
        # Update the accuracy metric
        accuracy_metric.update_state(y_batch_train, logits)

        # Log the loss and accuracy every 200 steps
        if step % 200 == 0:
            print(f'Epoch {epoch + 1} Step {step}: Loss = {loss_value.numpy()} Accuracy = {accuracy_metric.result().numpy()}')
    
    # Reset the metric at the end of each epoch
    accuracy_metric.reset_state()


Start of epoch 1
Epoch 1 Step 0: Loss = 2.3989651203155518 Accuracy = 0.125
Epoch 1 Step 200: Loss = 0.39067143201828003 Accuracy = 0.8300684094429016
Epoch 1 Step 400: Loss = 0.2013072520494461 Accuracy = 0.8639339208602905
Epoch 1 Step 600: Loss = 0.14259469509124756 Accuracy = 0.8804076313972473
Epoch 1 Step 800: Loss = 0.1568191945552826 Accuracy = 0.8926342129707336
Epoch 1 Step 1000: Loss = 0.461900532245636 Accuracy = 0.9000687003135681
Epoch 1 Step 1200: Loss = 0.14780272543430328 Accuracy = 0.9066923260688782
Epoch 1 Step 1400: Loss = 0.21249328553676605 Accuracy = 0.9116479158401489
Epoch 1 Step 1600: Loss = 0.22185289859771729 Accuracy = 0.9150530695915222
Epoch 1 Step 1800: Loss = 0.17369922995567322 Accuracy = 0.9193329811096191


2025-05-17 12:32:17.260424: W tensorflow/core/framework/local_rendezvous.cc:404] Local rendezvous is aborting with status: OUT_OF_RANGE: End of sequence


Start of epoch 2
Epoch 2 Step 0: Loss = 0.07252101600170135 Accuracy = 1.0
Epoch 2 Step 200: Loss = 0.1536918580532074 Accuracy = 0.9625310897827148
Epoch 2 Step 400: Loss = 0.10757894814014435 Accuracy = 0.9582294225692749
Epoch 2 Step 600: Loss = 0.04298770800232887 Accuracy = 0.960170567035675
Epoch 2 Step 800: Loss = 0.06304651498794556 Accuracy = 0.9610642790794373
Epoch 2 Step 1000: Loss = 0.2755340337753296 Accuracy = 0.9612886905670166
Epoch 2 Step 1200: Loss = 0.07553431391716003 Accuracy = 0.9620628356933594
Epoch 2 Step 1400: Loss = 0.15110114216804504 Accuracy = 0.9626829028129578
Epoch 2 Step 1600: Loss = 0.13285812735557556 Accuracy = 0.9626210331916809
Epoch 2 Step 1800: Loss = 0.12450723350048065 Accuracy = 0.9635445475578308


2025-05-17 12:32:31.561529: W tensorflow/core/framework/local_rendezvous.cc:404] Local rendezvous is aborting with status: OUT_OF_RANGE: End of sequence


Start of epoch 3
Epoch 3 Step 0: Loss = 0.033684682101011276 Accuracy = 1.0
Epoch 3 Step 200: Loss = 0.08016777783632278 Accuracy = 0.9751243591308594
Epoch 3 Step 400: Loss = 0.09115833044052124 Accuracy = 0.9742051362991333
Epoch 3 Step 600: Loss = 0.028054453432559967 Accuracy = 0.9750936031341553
Epoch 3 Step 800: Loss = 0.02326233871281147 Accuracy = 0.9749531745910645
Epoch 3 Step 1000: Loss = 0.17429952323436737 Accuracy = 0.9752435088157654
Epoch 3 Step 1200: Loss = 0.03849416598677635 Accuracy = 0.9755932688713074
Epoch 3 Step 1400: Loss = 0.10121943801641464 Accuracy = 0.975731611251831
Epoch 3 Step 1600: Loss = 0.0625501424074173 Accuracy = 0.9755231142044067
Epoch 3 Step 1800: Loss = 0.10478781908750534 Accuracy = 0.975985586643219


2025-05-17 12:32:45.014997: W tensorflow/core/framework/local_rendezvous.cc:404] Local rendezvous is aborting with status: OUT_OF_RANGE: End of sequence


Start of epoch 4
Epoch 4 Step 0: Loss = 0.01810392551124096 Accuracy = 1.0
Epoch 4 Step 200: Loss = 0.03600374981760979 Accuracy = 0.9827425479888916
Epoch 4 Step 400: Loss = 0.05090842396020889 Accuracy = 0.9819201827049255
Epoch 4 Step 600: Loss = 0.03503746911883354 Accuracy = 0.9827890992164612
Epoch 4 Step 800: Loss = 0.013914085924625397 Accuracy = 0.9823268055915833
Epoch 4 Step 1000: Loss = 0.1313038170337677 Accuracy = 0.982361376285553
Epoch 4 Step 1200: Loss = 0.03307771310210228 Accuracy = 0.982358455657959
Epoch 4 Step 1400: Loss = 0.06165098398923874 Accuracy = 0.9825794100761414
Epoch 4 Step 1600: Loss = 0.030330155044794083 Accuracy = 0.9824914336204529
Epoch 4 Step 1800: Loss = 0.09285018593072891 Accuracy = 0.9825964570045471


2025-05-17 12:32:58.400882: W tensorflow/core/framework/local_rendezvous.cc:404] Local rendezvous is aborting with status: OUT_OF_RANGE: End of sequence


Start of epoch 5
Epoch 5 Step 0: Loss = 0.019151700660586357 Accuracy = 1.0
Epoch 5 Step 200: Loss = 0.019217411056160927 Accuracy = 0.9875621795654297
Epoch 5 Step 400: Loss = 0.03194243460893631 Accuracy = 0.9870635867118835
Epoch 5 Step 600: Loss = 0.05437399074435234 Accuracy = 0.987936794757843
Epoch 5 Step 800: Loss = 0.013504350557923317 Accuracy = 0.9875546097755432
Epoch 5 Step 1000: Loss = 0.1255546510219574 Accuracy = 0.9875749349594116
Epoch 5 Step 1200: Loss = 0.02562267892062664 Accuracy = 0.9877185821533203
Epoch 5 Step 1400: Loss = 0.030695758759975433 Accuracy = 0.9875758290290833
Epoch 5 Step 1600: Loss = 0.013527502305805683 Accuracy = 0.9873906970024109
Epoch 5 Step 1800: Loss = 0.08517139405012131 Accuracy = 0.9875242710113525


2025-05-17 12:33:12.993504: W tensorflow/core/framework/local_rendezvous.cc:404] Local rendezvous is aborting with status: OUT_OF_RANGE: End of sequence


### Exercise 3: Custom Callback for Advanced Logging: 

Implement a custom callback to log additional metrics and information during training. 

#### 1. Set Up the Environment: 

Follow the setup from Exercise 1.


In [5]:
import tensorflow as tf 
from tensorflow.keras.models import Sequential 
from tensorflow.keras.layers import Dense, Flatten 

# Step 1: Set Up the Environment
(x_train, y_train), (x_test, y_test) = tf.keras.datasets.mnist.load_data()

# Normalize the pixel values to be between 0 and 1
x_train, x_test = x_train / 255.0, x_test / 255.0 

# Create a batched dataset for training
train_dataset = tf.data.Dataset.from_tensor_slices((x_train, y_train)).batch(32)


#### 2. Define the Model: 

Use the same model as in Exercise 1. 


In [6]:
# Step 2: Define the Model

model = Sequential([
    Flatten(input_shape=(28, 28)),  # Flatten the input to a 1D vector
    Dense(128, activation='relu'),  # First hidden layer with 128 neurons and ReLU activation
    Dense(10)  # Output layer with 10 neurons for the 10 classes (digits 0-9)
])


#### 3. Define Loss Function, Optimizer, and Metric: 

- Use Sparse Categorical Crossentropy for the loss function and Adam optimizer. 

- Add Sparse Categorical Accuracy as a metric. 


In [7]:
# Step 3: Define Loss Function, Optimizer, and Metric

loss_fn = tf.keras.losses.SparseCategoricalCrossentropy(from_logits=True)  # Loss function for multi-class classification
optimizer = tf.keras.optimizers.Adam()  # Adam optimizer for efficient training
accuracy_metric = tf.keras.metrics.SparseCategoricalAccuracy()  # Metric to track accuracy during training


#### 4. Implement the custom training loop with custom callback: 

Create a custom callback to log additional metrics at the end of each epoch.


In [8]:
from tensorflow.keras.callbacks import Callback

# Step 4: Implement the Custom Callback 
class CustomCallback(Callback):
    def on_epoch_end(self, epoch, logs=None):
        logs = logs or {}
        print(f'End of epoch {epoch + 1}, loss: {logs.get("loss")}, accuracy: {logs.get("accuracy")}')


In [9]:
# Step 5: Implement the Custom Training Loop with Custom Callback

epochs = 2
custom_callback = CustomCallback()  # Initialize the custom callback

for epoch in range(epochs):
    print(f'Start of epoch {epoch + 1}')
    
    for step, (x_batch_train, y_batch_train) in enumerate(train_dataset):
        with tf.GradientTape() as tape:
            # Forward pass: Compute predictions
            logits = model(x_batch_train, training=True)
            # Compute loss
            loss_value = loss_fn(y_batch_train, logits)
        
        # Compute gradients
        grads = tape.gradient(loss_value, model.trainable_weights)
        # Apply gradients to update model weights
        optimizer.apply_gradients(zip(grads, model.trainable_weights))
        
        # Update the accuracy metric
        accuracy_metric.update_state(y_batch_train, logits)

        # Log the loss and accuracy every 200 steps
        if step % 200 == 0:
            print(f'Epoch {epoch + 1} Step {step}: Loss = {loss_value.numpy()} Accuracy = {accuracy_metric.result().numpy()}')
    
    # Call the custom callback at the end of each epoch
    custom_callback.on_epoch_end(epoch, logs={'loss': loss_value.numpy(), 'accuracy': accuracy_metric.result().numpy()})
    
    # Reset the metric at the end of each epoch
    accuracy_metric.reset_state()  # Use reset_state() instead of reset_states()


Start of epoch 1
Epoch 1 Step 0: Loss = 2.326517105102539 Accuracy = 0.0625
Epoch 1 Step 200: Loss = 0.40959733724594116 Accuracy = 0.8411069512367249
Epoch 1 Step 400: Loss = 0.17708174884319305 Accuracy = 0.8703241944313049
Epoch 1 Step 600: Loss = 0.18139535188674927 Accuracy = 0.8844113945960999
Epoch 1 Step 800: Loss = 0.17153844237327576 Accuracy = 0.896496593952179
Epoch 1 Step 1000: Loss = 0.43492043018341064 Accuracy = 0.9036900401115417
Epoch 1 Step 1200: Loss = 0.17387041449546814 Accuracy = 0.9101790189743042
Epoch 1 Step 1400: Loss = 0.22246310114860535 Accuracy = 0.9151722192764282
Epoch 1 Step 1600: Loss = 0.25185179710388184 Accuracy = 0.9184103608131409
Epoch 1 Step 1800: Loss = 0.14886173605918884 Accuracy = 0.9223001003265381


2025-05-17 12:33:46.028869: W tensorflow/core/framework/local_rendezvous.cc:404] Local rendezvous is aborting with status: OUT_OF_RANGE: End of sequence


End of epoch 1, loss: 0.04910638928413391, accuracy: 0.9242833256721497
Start of epoch 2
Epoch 2 Step 0: Loss = 0.05975966528058052 Accuracy = 1.0
Epoch 2 Step 200: Loss = 0.11801654100418091 Accuracy = 0.9629974961280823
Epoch 2 Step 400: Loss = 0.0905696377158165 Accuracy = 0.9595542550086975
Epoch 2 Step 600: Loss = 0.04465322196483612 Accuracy = 0.9626144170761108
Epoch 2 Step 800: Loss = 0.10440795123577118 Accuracy = 0.9627419114112854
Epoch 2 Step 1000: Loss = 0.21767809987068176 Accuracy = 0.9628496766090393
Epoch 2 Step 1200: Loss = 0.10654351115226746 Accuracy = 0.9635720252990723
Epoch 2 Step 1400: Loss = 0.1161811575293541 Accuracy = 0.9642443060874939
Epoch 2 Step 1600: Loss = 0.18140846490859985 Accuracy = 0.9641239643096924
Epoch 2 Step 1800: Loss = 0.09486439824104309 Accuracy = 0.9647418260574341
End of epoch 2, loss: 0.05387478694319725, accuracy: 0.965499997138977


2025-05-17 12:34:00.849427: W tensorflow/core/framework/local_rendezvous.cc:404] Local rendezvous is aborting with status: OUT_OF_RANGE: End of sequence


### Exercise 4: Add Hidden Layers 

Next, you will add a couple of hidden layers to your model. Hidden layers help the model learn complex patterns in the data. 


In [10]:
from tensorflow.keras.layers import Input, Dense

# Define the input layer
input_layer = Input(shape=(28, 28))  # Input layer with shape (28, 28)

# Define hidden layers
hidden_layer1 = Dense(64, activation='relu')(input_layer)  # First hidden layer with 64 neurons and ReLU activation
hidden_layer2 = Dense(64, activation='relu')(hidden_layer1)  # Second hidden layer with 64 neurons and ReLU activation


In the above code: 

`Dense(64, activation='relu')` creates a dense (fully connected) layer with 64 units and ReLU activation function. 

Each hidden layer takes the output of the previous layer as its input.


### Exercise 5: Define the output layer 

Finally, you will define the output layer. Suppose you are working on a binary classification problem, so the output layer will have one unit with a sigmoid activation function. 


In [11]:
output_layer = Dense(1, activation='sigmoid')(hidden_layer2)

In the above code: 

`Dense(1, activation='sigmoid')` creates a dense layer with 1 unit and a sigmoid activation function, suitable for binary classification. 


### Exercise 6: Create the Model 

Now, you will create the model by specifying the input and output layers. 


In [20]:
from tensorflow.keras.models import Model
model = Model(inputs=input_layer, outputs=output_layer)

In the above code: 

`Model(inputs=input_layer, outputs=output_layer)` creates a Keras model that connects the input layer to the output layer through the hidden layers. 


### Exercise 7: Compile the Model 

Before training the model, you need to compile it. You will specify the loss function, optimizer, and evaluation metrics. 


In [21]:
model.compile(optimizer='adam', loss='binary_crossentropy', metrics=['accuracy'])

In the above code: 

`optimizer='adam'` specifies the Adam optimizer, a popular choice for training neural networks. 

`loss='binary_crossentropy'` specifies the loss function for binary classification problems. 

`metrics=['accuracy']` tells Keras to evaluate the model using accuracy during training. 


### Exercise 8: Train the Model 

You can now train the model on some training data. For this example, let's assume `X_train` is our training input data and `y_train` is the corresponding labels. 


In [22]:
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, Input
import numpy as np

# Step 1: Redefine the Model for 20 features
model = Sequential([
    Input(shape=(20,)),  # Adjust input shape to (20,)
    Dense(128, activation='relu'),  # Hidden layer with 128 neurons and ReLU activation
    Dense(1, activation='sigmoid')  # Output layer for binary classification with sigmoid activation
])

# Compile the model
model.compile(optimizer='adam', loss='binary_crossentropy', metrics=['accuracy'])

# Step 2: Generate Example Data
X_train = np.random.rand(1000, 20)  # 1000 samples, 20 features each
y_train = np.random.randint(2, size=(1000, 1))  # 1000 binary labels (0 or 1)

# Step 3: Train the Model
model.fit(X_train, y_train, epochs=10, batch_size=32)

Epoch 1/10
32/32 ━━━━━━━━━━━━━━━━━━━━ 0s 918us/step - accuracy: 0.5009 - loss: 0.6969 
Epoch 2/10
32/32 ━━━━━━━━━━━━━━━━━━━━ 0s 938us/step - accuracy: 0.5281 - loss: 0.6891
Epoch 3/10
32/32 ━━━━━━━━━━━━━━━━━━━━ 0s 870us/step - accuracy: 0.5604 - loss: 0.6847
Epoch 4/10
32/32 ━━━━━━━━━━━━━━━━━━━━ 0s 855us/step - accuracy: 0.5748 - loss: 0.6843
Epoch 5/10
32/32 ━━━━━━━━━━━━━━━━━━━━ 0s 862us/step - accuracy: 0.5638 - loss: 0.6812
Epoch 6/10
32/32 ━━━━━━━━━━━━━━━━━━━━ 0s 868us/step - accuracy: 0.5813 - loss: 0.6781
Epoch 7/10
32/32 ━━━━━━━━━━━━━━━━━━━━ 0s 844us/step - accuracy: 0.5816 - loss: 0.6744
Epoch 8/10
32/32 ━━━━━━━━━━━━━━━━━━━━ 0s 814us/step - accuracy: 0.5525 - loss: 0.6837
Epoch 9/10
32/32 ━━━━━━━━━━━━━━━━━━━━ 0s 818us/step - accuracy: 0.5788 - loss: 0.6801
Epoch 10/10
32/32 ━━━━━━━━━━━━━━━━━━━━ 0s 841us/step - accuracy: 0.5871 - loss: 0.6761


In the above code: 

`X_train` and `y_train` are placeholders for your actual training data. 

`model.fit` trains the model for a specified number of epochs and batch size. 


### Exercise 9: Evaluate the Model 

After training, you can evaluate the model on test data to see how well it performs. 


In [23]:
# Example test data (in practice, use real dataset)
X_test = np.random.rand(200, 20)  # 200 samples, 20 features each
y_test = np.random.randint(2, size=(200, 1))  # 200 binary labels (0 or 1)

# Evaluate the model on the test data
loss, accuracy = model.evaluate(X_test, y_test)

# Print test loss and accuracy
print(f'Test loss: {loss}')
print(f'Test accuracy: {accuracy}')


7/7 ━━━━━━━━━━━━━━━━━━━━ 0s 2ms/step - accuracy: 0.5149 - loss: 0.6961 
Test loss: 0.7007125020027161
Test accuracy: 0.4950000047683716


In the above code: 

`model.evaluate` computes the loss and accuracy of the model on test data. 

`X_test` and `y_test` are placeholders for your actual test data. 


## Practice Exercises 

### Exercise 1: Basic Custom Training Loop 

#### Objective: Implement a basic custom training loop to train a simple neural network on the MNIST dataset. 

#### Instructions: 

- Set up the environment and load the dataset. 

- Define the model with a Flatten layer and two Dense layers. 

- Define the loss function and optimizer. 

- Implement a custom training loop to iterate over the dataset, compute the loss, and update the model's weights. 


In [25]:
import tensorflow

In [28]:
# Write your code here
model1=Sequential([Flatten(input_shape=(28,28)),Dense(128,activation='relu'),Dense(10)])
lossfn1=tensorflow.keras.losses.SparseCategoricalCrossentropy(from_logits=True)
optimizer1=tensorflow.keras.optimizers.Adam()
for epoch in range(10):
    for x_batch, y_batch in train_dataset:
        with tensorflow.GradientTape() as tape:
            logits=model1(x_batch,training=True)
            loss=lossfn1(y_batch,logits)
            grads=tape.gradient(loss,model1.trainable_weights)
            optimizer1.apply_gradients(zip(grads,model1.trainable_weights))
        print(f'Epoch number {epoch+1}: Loss = {loss.numpy()}')


/Users/govindswarooprahangdale/tfenv/lib/python3.10/site-packages/keras/src/layers/reshaping/flatten.py:37: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(**kwargs)


Epoch number 1: Loss = 2.396927833557129
Epoch number 1: Loss = 2.358563184738159
Epoch number 1: Loss = 2.2371349334716797
Epoch number 1: Loss = 1.9800719022750854
Epoch number 1: Loss = 2.072115421295166
Epoch number 1: Loss = 2.0635128021240234
Epoch number 1: Loss = 1.754390835762024
Epoch number 1: Loss = 1.7606086730957031
Epoch number 1: Loss = 1.9061919450759888
Epoch number 1: Loss = 1.5886039733886719
Epoch number 1: Loss = 1.6627591848373413
Epoch number 1: Loss = 1.503139615058899
Epoch number 1: Loss = 1.632433533668518
Epoch number 1: Loss = 1.4343593120574951
Epoch number 1: Loss = 1.230912208557129
Epoch number 1: Loss = 1.622351050376892
Epoch number 1: Loss = 1.566413164138794
Epoch number 1: Loss = 1.2348442077636719
Epoch number 1: Loss = 1.4753904342651367
Epoch number 1: Loss = 1.455950140953064
Epoch number 1: Loss = 1.3982510566711426
Epoch number 1: Loss = 1.134670376777649
Epoch number 1: Loss = 1.1657319068908691
Epoch number 1: Loss = 1.1884651184082031
Epo

2025-05-17 12:56:37.066725: W tensorflow/core/framework/local_rendezvous.cc:404] Local rendezvous is aborting with status: OUT_OF_RANGE: End of sequence


Epoch number 2: Loss = 0.05259983241558075
Epoch number 2: Loss = 0.3290615975856781
Epoch number 2: Loss = 0.12858092784881592
Epoch number 2: Loss = 0.35381150245666504
Epoch number 2: Loss = 0.04260749742388725
Epoch number 2: Loss = 0.1544240117073059
Epoch number 2: Loss = 0.16005021333694458
Epoch number 2: Loss = 0.4227098226547241
Epoch number 2: Loss = 0.2970776855945587
Epoch number 2: Loss = 0.23317743837833405
Epoch number 2: Loss = 0.3332206606864929
Epoch number 2: Loss = 0.04466522857546806
Epoch number 2: Loss = 0.1369829773902893
Epoch number 2: Loss = 0.4856606423854828
Epoch number 2: Loss = 0.11409200727939606
Epoch number 2: Loss = 0.11780530959367752
Epoch number 2: Loss = 0.15409065783023834
Epoch number 2: Loss = 0.44085001945495605
Epoch number 2: Loss = 0.28856247663497925
Epoch number 2: Loss = 0.07844546437263489
Epoch number 2: Loss = 0.04031781852245331
Epoch number 2: Loss = 0.04774126783013344
Epoch number 2: Loss = 0.17560380697250366
Epoch number 2: Lo

2025-05-17 12:56:51.189973: W tensorflow/core/framework/local_rendezvous.cc:404] Local rendezvous is aborting with status: OUT_OF_RANGE: End of sequence


...

2025-05-17 12:58:12.941617: W tensorflow/core/framework/local_rendezvous.cc:404] Local rendezvous is aborting with status: OUT_OF_RANGE: End of sequence


Epoch number 9: Loss = 0.006700438447296619
Epoch number 9: Loss = 0.006665341556072235
Epoch number 9: Loss = 0.0005664266063831747
Epoch number 9: Loss = 0.03376050293445587
Epoch number 9: Loss = 0.014571299776434898
Epoch number 9: Loss = 0.033418312668800354
Epoch number 9: Loss = 0.013745998032391071
Epoch number 9: Loss = 0.017503898590803146
Epoch number 9: Loss = 0.004761852324008942
Epoch number 9: Loss = 0.013235248625278473
Epoch number 9: Loss = 0.004871830344200134
Epoch number 9: Loss = 0.008146924898028374
Epoch number 9: Loss = 0.05410383269190788
Epoch number 9: Loss = 0.05310104042291641
Epoch number 9: Loss = 0.008551504462957382
Epoch number 9: Loss = 0.016811111941933632
Epoch number 9: Loss = 0.011747579090297222
Epoch number 9: Loss = 0.007994852028787136
Epoch number 9: Loss = 0.07003870606422424
Epoch number 9: Loss = 0.06877591460943222
Epoch number 9: Loss = 0.003152225399389863
Epoch number 9: Loss = 0.0033430266194045544
Epoch number 9: Loss = 0.0112455086

2025-05-17 12:58:26.945277: W tensorflow/core/framework/local_rendezvous.cc:404] Local rendezvous is aborting with status: OUT_OF_RANGE: End of sequence


Epoch number 10: Loss = 0.013872243463993073
Epoch number 10: Loss = 0.00716437166556716
Epoch number 10: Loss = 0.18586209416389465
Epoch number 10: Loss = 0.01999025046825409
Epoch number 10: Loss = 0.019587529823184013
Epoch number 10: Loss = 0.039641160517930984
Epoch number 10: Loss = 0.018763087689876556
Epoch number 10: Loss = 0.014082844369113445
Epoch number 10: Loss = 0.000569365918636322
Epoch number 10: Loss = 0.02081984654068947
Epoch number 10: Loss = 0.008946727029979229
Epoch number 10: Loss = 0.013542878441512585
Epoch number 10: Loss = 0.003685643430799246
Epoch number 10: Loss = 0.006742745637893677
Epoch number 10: Loss = 0.0021420326083898544
Epoch number 10: Loss = 0.05792321637272835
Epoch number 10: Loss = 0.009398829191923141
Epoch number 10: Loss = 0.007034383714199066
Epoch number 10: Loss = 0.026539213955402374
Epoch number 10: Loss = 0.05025358125567436
Epoch number 10: Loss = 0.012636268511414528
Epoch number 10: Loss = 0.025691935792565346
Epoch number 10

2025-05-17 12:58:40.268219: W tensorflow/core/framework/local_rendezvous.cc:404] Local rendezvous is aborting with status: OUT_OF_RANGE: End of sequence


<details>
<summary>Click here for solution</summary> </br>

```python
# Import necessary libraries
import tensorflow as tf 
from tensorflow.keras.models import Sequential 
from tensorflow.keras.layers import Dense, Flatten 

# Step 1: Set Up the Environment
(x_train, y_train), (x_test, y_test) = tf.keras.datasets.mnist.load_data() 
x_train, x_test = x_train / 255.0, x_test / 255.0 
train_dataset = tf.data.Dataset.from_tensor_slices((x_train, y_train)).batch(32) 

# Step 2: Define the Model
model = Sequential([ 
    Flatten(input_shape=(28, 28)), 
    Dense(128, activation='relu'), 
    Dense(10) 
]) 

# Step 3: Define Loss Function and Optimizer
loss_fn = tf.keras.losses.SparseCategoricalCrossentropy(from_logits=True) 
optimizer = tf.keras.optimizers.Adam() 

# Step 4: Implement the Custom Training Loop
for epoch in range(5): 
    for x_batch, y_batch in train_dataset: 
        with tf.GradientTape() as tape: 
            logits = model(x_batch, training=True) 
            loss = loss_fn(y_batch, logits) 
        grads = tape.gradient(loss, model.trainable_weights) 
        optimizer.apply_gradients(zip(grads, model.trainable_weights)) 
    print(f'Epoch {epoch + 1}: Loss = {loss.numpy()}')


### Exercise 2: Adding Accuracy Metric 

#### Objective: Enhance the custom training loop by adding an accuracy metric to monitor model performance. 

#### Instructions: 

1. Set up the environment and define the model, loss function, and optimizer. 

2. Add Sparse Categorical Accuracy as a metric. 

3. Implement the custom training loop with accuracy tracking.


In [30]:
# Write your code here
accuracy_metric=tensorflow.keras.metrics.SparseCategoricalAccuracy()
for epoch in range(10):
    for x_batch, y_batch in train_dataset:
        with tensorflow.GradientTape() as tape:
            logits=model1(x_batch,training=True)
            loss=lossfn1(y_batch,logits)
            grads=tape.gradient(loss,model1.trainable_weights)
            optimizer1.apply_gradients(zip(grads,model1.trainable_weights))
            accuracy_metric.update_state(y_batch,logits)
        print(f'Epoch number {epoch+1}: Loss = {loss.numpy()} and Accuracy = {accuracy_metric.result().numpy()}')
        accuracy_metric.reset_state()

Epoch number 1: Loss = 0.0024009773042052984 and Accuracy = 1.0
Epoch number 1: Loss = 0.004174304194748402 and Accuracy = 1.0
Epoch number 1: Loss = 0.0013895666925236583 and Accuracy = 1.0
Epoch number 1: Loss = 0.0009857055265456438 and Accuracy = 1.0
Epoch number 1: Loss = 0.033651839941740036 and Accuracy = 1.0
Epoch number 1: Loss = 0.01133019756525755 and Accuracy = 1.0
Epoch number 1: Loss = 0.013013308867812157 and Accuracy = 1.0
Epoch number 1: Loss = 0.003051473293453455 and Accuracy = 1.0
Epoch number 1: Loss = 0.006167102605104446 and Accuracy = 1.0
Epoch number 1: Loss = 0.00012775647337548435 and Accuracy = 1.0
Epoch number 1: Loss = 0.00017176559776999056 and Accuracy = 1.0
Epoch number 1: Loss = 0.003396477084606886 and Accuracy = 1.0
Epoch number 1: Loss = 0.002146263374015689 and Accuracy = 1.0
Epoch number 1: Loss = 0.00837302953004837 and Accuracy = 1.0
Epoch number 1: Loss = 0.003992818761616945 and Accuracy = 1.0
Epoch number 1: Loss = 0.04601414501667023 and Acc

2025-05-17 13:03:00.846942: W tensorflow/core/framework/local_rendezvous.cc:404] Local rendezvous is aborting with status: OUT_OF_RANGE: End of sequence


Epoch number 2: Loss = 0.002023885725066066 and Accuracy = 1.0
Epoch number 2: Loss = 0.03894869238138199 and Accuracy = 0.96875
Epoch number 2: Loss = 0.029751086607575417 and Accuracy = 0.96875
Epoch number 2: Loss = 0.00828517135232687 and Accuracy = 1.0
Epoch number 2: Loss = 0.002452430548146367 and Accuracy = 1.0
Epoch number 2: Loss = 0.006994353141635656 and Accuracy = 1.0
Epoch number 2: Loss = 0.0002066380257019773 and Accuracy = 1.0
Epoch number 2: Loss = 0.0006695775082334876 and Accuracy = 1.0
Epoch number 2: Loss = 0.0012975826393812895 and Accuracy = 1.0
Epoch number 2: Loss = 0.009213963523507118 and Accuracy = 1.0
Epoch number 2: Loss = 0.045549176633358 and Accuracy = 0.96875
Epoch number 2: Loss = 0.00485211843624711 and Accuracy = 1.0
Epoch number 2: Loss = 0.018272096291184425 and Accuracy = 1.0
Epoch number 2: Loss = 0.01763334684073925 and Accuracy = 1.0
Epoch number 2: Loss = 0.001877784263342619 and Accuracy = 1.0
Epoch number 2: Loss = 0.0028352891094982624 an

2025-05-17 13:03:17.141305: W tensorflow/core/framework/local_rendezvous.cc:404] Local rendezvous is aborting with status: OUT_OF_RANGE: End of sequence


Epoch number 3: Loss = 0.0063141705468297005 and Accuracy = 1.0
Epoch number 3: Loss = 0.046068333089351654 and Accuracy = 0.96875
Epoch number 3: Loss = 0.011844854801893234 and Accuracy = 1.0
Epoch number 3: Loss = 0.05627928674221039 and Accuracy = 0.96875
Epoch number 3: Loss = 0.001627076300792396 and Accuracy = 1.0
Epoch number 3: Loss = 0.0019762148149311543 and Accuracy = 1.0
Epoch number 3: Loss = 0.022277314215898514 and Accuracy = 1.0
Epoch number 3: Loss = 0.004345436114817858 and Accuracy = 1.0
Epoch number 3: Loss = 5.406795389717445e-05 and Accuracy = 1.0
Epoch number 3: Loss = 0.00010124570690095425 and Accuracy = 1.0
Epoch number 3: Loss = 0.003786854911595583 and Accuracy = 1.0
Epoch number 3: Loss = 0.004232389852404594 and Accuracy = 1.0
Epoch number 3: Loss = 0.00590486079454422 and Accuracy = 1.0
Epoch number 3: Loss = 0.002360632875934243 and Accuracy = 1.0
Epoch number 3: Loss = 0.036361776292324066 and Accuracy = 0.96875
Epoch number 3: Loss = 0.006255494430661

...

2025-05-17 13:04:55.377960: W tensorflow/core/framework/local_rendezvous.cc:404] Local rendezvous is aborting with status: OUT_OF_RANGE: End of sequence


Epoch number 9: Loss = 0.00011301897029625252 and Accuracy = 1.0
Epoch number 9: Loss = 0.00016308804333675653 and Accuracy = 1.0
Epoch number 9: Loss = 0.000940923229791224 and Accuracy = 1.0
Epoch number 9: Loss = 0.00012705204426310956 and Accuracy = 1.0
Epoch number 9: Loss = 8.45520626171492e-05 and Accuracy = 1.0
Epoch number 9: Loss = 0.0002641043101903051 and Accuracy = 1.0
Epoch number 9: Loss = 0.0057096644304692745 and Accuracy = 1.0
Epoch number 9: Loss = 0.0012636675965040922 and Accuracy = 1.0
Epoch number 9: Loss = 0.004555635154247284 and Accuracy = 1.0
Epoch number 9: Loss = 0.0031899120658636093 and Accuracy = 1.0
Epoch number 9: Loss = 0.0017837502527981997 and Accuracy = 1.0
Epoch number 9: Loss = 0.0012521438766270876 and Accuracy = 1.0
Epoch number 9: Loss = 0.0008110512280836701 and Accuracy = 1.0
Epoch number 9: Loss = 0.004903778899461031 and Accuracy = 1.0
Epoch number 9: Loss = 0.0009390224004164338 and Accuracy = 1.0
Epoch number 9: Loss = 4.995086055714637e

2025-05-17 13:05:12.452750: W tensorflow/core/framework/local_rendezvous.cc:404] Local rendezvous is aborting with status: OUT_OF_RANGE: End of sequence


Epoch number 10: Loss = 0.008606906048953533 and Accuracy = 1.0
Epoch number 10: Loss = 5.2466530178207904e-05 and Accuracy = 1.0
Epoch number 10: Loss = 0.0009000995196402073 and Accuracy = 1.0
Epoch number 10: Loss = 6.866751937195659e-05 and Accuracy = 1.0
Epoch number 10: Loss = 0.005399009212851524 and Accuracy = 1.0
Epoch number 10: Loss = 0.002471628598868847 and Accuracy = 1.0
Epoch number 10: Loss = 0.0006663333042524755 and Accuracy = 1.0
Epoch number 10: Loss = 0.0013146810233592987 and Accuracy = 1.0
Epoch number 10: Loss = 0.00015461606380995363 and Accuracy = 1.0
Epoch number 10: Loss = 0.0032537474762648344 and Accuracy = 1.0
Epoch number 10: Loss = 0.00011359424388501793 and Accuracy = 1.0
Epoch number 10: Loss = 0.013249796815216541 and Accuracy = 1.0
Epoch number 10: Loss = 2.497258537914604e-05 and Accuracy = 1.0
Epoch number 10: Loss = 0.027946267277002335 and Accuracy = 1.0
Epoch number 10: Loss = 2.668242268555332e-05 and Accuracy = 1.0
Epoch number 10: Loss = 5.1

2025-05-17 13:05:28.171840: W tensorflow/core/framework/local_rendezvous.cc:404] Local rendezvous is aborting with status: OUT_OF_RANGE: End of sequence


<details>
<summary>Click here for solution</summary><br>

```python
# Import necessary libraries
import tensorflow as tf 
from tensorflow.keras.models import Sequential 
from tensorflow.keras.layers import Dense, Flatten 

# Step 1: Set Up the Environment
(x_train, y_train), _ = tf.keras.datasets.mnist.load_data() 
x_train = x_train / 255.0 
train_dataset = tf.data.Dataset.from_tensor_slices((x_train, y_train)).batch(32) 

# Step 2: Define the Model
model = Sequential([ 
    Flatten(input_shape=(28, 28)), 
    Dense(128, activation='relu'), 
    Dense(10) 
]) 

# Step 3: Define Loss Function, Optimizer, and Metric
loss_fn = tf.keras.losses.SparseCategoricalCrossentropy(from_logits=True) 
optimizer = tf.keras.optimizers.Adam() 
accuracy_metric = tf.keras.metrics.SparseCategoricalAccuracy() 

# Step 4: Implement the Custom Training Loop with Accuracy Tracking
epochs = 5 
for epoch in range(epochs): 
    for x_batch, y_batch in train_dataset: 
        with tf.GradientTape() as tape: 
            logits = model(x_batch, training=True) 
            loss = loss_fn(y_batch, logits) 
        grads = tape.gradient(loss, model.trainable_weights) 
        optimizer.apply_gradients(zip(grads, model.trainable_weights)) 
        accuracy_metric.update_state(y_batch, logits) 
    print(f'Epoch {epoch + 1}: Loss = {loss.numpy()} Accuracy = {accuracy_metric.result().numpy()}') 
    accuracy_metric.reset_state() 


### Exercise 3: Custom Callback for Advanced Logging 

#### Objective: Implement a custom callback to log additional metrics and information during training. 

#### Instructions: 

1. Set up the environment and define the model, loss function, optimizer, and metric. 

2. Create a custom callback to log additional metrics at the end of each epoch. 

3. Implement the custom training loop with the custom callback. 


In [32]:
# Write your code here
model2=Sequential([tensorflow.keras.Input(shape=(28,28)),Flatten(),Dense(128,activation='relu'),Dense(10)])
loss_fn = tf.keras.losses.SparseCategoricalCrossentropy(from_logits=True) 
optimizer = tf.keras.optimizers.Adam() 
accuracy_metric = tf.keras.metrics.SparseCategoricalAccuracy() 

# Step 4: Implement the Custom Callback
class CustomCallback(Callback): 
    def on_epoch_end(self, epoch, logs=None): 
        print(f'End of epoch {epoch + 1}, loss: {logs.get("loss")}, accuracy: {logs.get("accuracy")}') 

# Step 5: Implement the Custom Training Loop with Custom Callback
custom_callback = CustomCallback() 
for epoch in range(10):
    for x_batch, y_batch in train_dataset:
        with tensorflow.GradientTape() as tape:
            logits=model1(x_batch,training=True)
            loss=lossfn1(y_batch,logits)
            grads=tape.gradient(loss,model1.trainable_weights)
            optimizer1.apply_gradients(zip(grads,model1.trainable_weights))
            accuracy_metric.update_state(y_batch,logits)
        print(f'Epoch number {epoch+1}: Loss = {loss.numpy()} and Accuracy = {accuracy_metric.result().numpy()}')
        custom_callback.on_epoch_end(epoch,logs={'loss':loss.numpy(),'accuracy':accuracy_metric.result().numpy()})
        accuracy_metric.reset_state()

Epoch number 1: Loss = 5.626641359413043e-05 and Accuracy = 1.0
End of epoch 1, loss: 5.626641359413043e-05, accuracy: 1.0
Epoch number 1: Loss = 0.0019819221924990416 and Accuracy = 1.0
End of epoch 1, loss: 0.0019819221924990416, accuracy: 1.0
Epoch number 1: Loss = 5.058737224317156e-05 and Accuracy = 1.0
End of epoch 1, loss: 5.058737224317156e-05, accuracy: 1.0
Epoch number 1: Loss = 5.088127727503888e-05 and Accuracy = 1.0
End of epoch 1, loss: 5.088127727503888e-05, accuracy: 1.0
Epoch number 1: Loss = 0.0008541302522644401 and Accuracy = 1.0
End of epoch 1, loss: 0.0008541302522644401, accuracy: 1.0
Epoch number 1: Loss = 0.008741225115954876 and Accuracy = 1.0
End of epoch 1, loss: 0.008741225115954876, accuracy: 1.0
Epoch number 1: Loss = 0.00010995898628607392 and Accuracy = 1.0
End of epoch 1, loss: 0.00010995898628607392, accuracy: 1.0
Epoch number 1: Loss = 0.0001791746763046831 and Accuracy = 1.0
End of epoch 1, loss: 0.0001791746763046831, accuracy: 1.0
Epoch number 1: 

2025-05-17 13:08:08.468935: W tensorflow/core/framework/local_rendezvous.cc:404] Local rendezvous is aborting with status: OUT_OF_RANGE: End of sequence


Epoch number 2: Loss = 0.005632362328469753 and Accuracy = 1.0
End of epoch 2, loss: 0.005632362328469753, accuracy: 1.0
Epoch number 2: Loss = 0.0010328579228371382 and Accuracy = 1.0
End of epoch 2, loss: 0.0010328579228371382, accuracy: 1.0
Epoch number 2: Loss = 0.0004396476433612406 and Accuracy = 1.0
End of epoch 2, loss: 0.0004396476433612406, accuracy: 1.0
Epoch number 2: Loss = 8.354946476174518e-05 and Accuracy = 1.0
End of epoch 2, loss: 8.354946476174518e-05, accuracy: 1.0
Epoch number 2: Loss = 0.0014916080981492996 and Accuracy = 1.0
End of epoch 2, loss: 0.0014916080981492996, accuracy: 1.0
Epoch number 2: Loss = 0.0007375780260190368 and Accuracy = 1.0
End of epoch 2, loss: 0.0007375780260190368, accuracy: 1.0
Epoch number 2: Loss = 0.0001506828557467088 and Accuracy = 1.0
End of epoch 2, loss: 0.0001506828557467088, accuracy: 1.0
Epoch number 2: Loss = 0.00012958861771039665 and Accuracy = 1.0
End of epoch 2, loss: 0.00012958861771039665, accuracy: 1.0
Epoch number 2: 

2025-05-17 13:08:25.579946: W tensorflow/core/framework/local_rendezvous.cc:404] Local rendezvous is aborting with status: OUT_OF_RANGE: End of sequence


Epoch number 3: Loss = 0.0042639425955712795 and Accuracy = 1.0
End of epoch 3, loss: 0.0042639425955712795, accuracy: 1.0
Epoch number 3: Loss = 0.00038322489126585424 and Accuracy = 1.0
End of epoch 3, loss: 0.00038322489126585424, accuracy: 1.0
Epoch number 3: Loss = 0.002921469509601593 and Accuracy = 1.0
End of epoch 3, loss: 0.002921469509601593, accuracy: 1.0
Epoch number 3: Loss = 0.04520554840564728 and Accuracy = 0.96875
End of epoch 3, loss: 0.04520554840564728, accuracy: 0.96875
Epoch number 3: Loss = 0.0004396569565869868 and Accuracy = 1.0
End of epoch 3, loss: 0.0004396569565869868, accuracy: 1.0
Epoch number 3: Loss = 6.747290899511427e-05 and Accuracy = 1.0
End of epoch 3, loss: 6.747290899511427e-05, accuracy: 1.0
Epoch number 3: Loss = 0.0020328524988144636 and Accuracy = 1.0
End of epoch 3, loss: 0.0020328524988144636, accuracy: 1.0
Epoch number 3: Loss = 0.025949055328965187 and Accuracy = 1.0
End of epoch 3, loss: 0.025949055328965187, accuracy: 1.0
Epoch number 3

...

2025-05-17 13:09:59.225684: W tensorflow/core/framework/local_rendezvous.cc:404] Local rendezvous is aborting with status: OUT_OF_RANGE: End of sequence


Epoch number 9: Loss = 0.0006994272698648274 and Accuracy = 1.0
End of epoch 9, loss: 0.0006994272698648274, accuracy: 1.0
Epoch number 9: Loss = 0.00954429805278778 and Accuracy = 1.0
End of epoch 9, loss: 0.00954429805278778, accuracy: 1.0
Epoch number 9: Loss = 8.653179975226521e-06 and Accuracy = 1.0
End of epoch 9, loss: 8.653179975226521e-06, accuracy: 1.0
Epoch number 9: Loss = 0.0002371547743678093 and Accuracy = 1.0
End of epoch 9, loss: 0.0002371547743678093, accuracy: 1.0
Epoch number 9: Loss = 8.701901606400497e-06 and Accuracy = 1.0
End of epoch 9, loss: 8.701901606400497e-06, accuracy: 1.0
Epoch number 9: Loss = 0.00023281019821297377 and Accuracy = 1.0
End of epoch 9, loss: 0.00023281019821297377, accuracy: 1.0
Epoch number 9: Loss = 5.997698053761269e-07 and Accuracy = 1.0
End of epoch 9, loss: 5.997698053761269e-07, accuracy: 1.0
Epoch number 9: Loss = 0.0002490237238816917 and Accuracy = 1.0
End of epoch 9, loss: 0.0002490237238816917, accuracy: 1.0
Epoch number 9: Lo

2025-05-17 13:10:14.197659: W tensorflow/core/framework/local_rendezvous.cc:404] Local rendezvous is aborting with status: OUT_OF_RANGE: End of sequence


Epoch number 10: Loss = 1.4666817151010036e-05 and Accuracy = 1.0
End of epoch 10, loss: 1.4666817151010036e-05, accuracy: 1.0
Epoch number 10: Loss = 1.0236304660793394e-05 and Accuracy = 1.0
End of epoch 10, loss: 1.0236304660793394e-05, accuracy: 1.0
Epoch number 10: Loss = 0.00010312359518138692 and Accuracy = 1.0
End of epoch 10, loss: 0.00010312359518138692, accuracy: 1.0
Epoch number 10: Loss = 0.0018719549989327788 and Accuracy = 1.0
End of epoch 10, loss: 0.0018719549989327788, accuracy: 1.0
Epoch number 10: Loss = 0.0006879385327920318 and Accuracy = 1.0
End of epoch 10, loss: 0.0006879385327920318, accuracy: 1.0
Epoch number 10: Loss = 0.000141716402140446 and Accuracy = 1.0
End of epoch 10, loss: 0.000141716402140446, accuracy: 1.0
Epoch number 10: Loss = 0.01168906781822443 and Accuracy = 1.0
End of epoch 10, loss: 0.01168906781822443, accuracy: 1.0
Epoch number 10: Loss = 2.2757281840313226e-05 and Accuracy = 1.0
End of epoch 10, loss: 2.2757281840313226e-05, accuracy: 1.

2025-05-17 13:10:29.082937: W tensorflow/core/framework/local_rendezvous.cc:404] Local rendezvous is aborting with status: OUT_OF_RANGE: End of sequence


<details>
<summary>Click here for solution</summary> </br>

```python
# Import necessary libraries
import tensorflow as tf 
from tensorflow.keras.models import Sequential 
from tensorflow.keras.layers import Dense, Flatten 
from tensorflow.keras.callbacks import Callback 

# Step 1: Set Up the Environment
(x_train, y_train), (x_test, y_test) = tf.keras.datasets.mnist.load_data() 
x_train = x_train / 255.0 
train_dataset = tf.data.Dataset.from_tensor_slices((x_train, y_train)).batch(32) 

# Step 2: Define the Model
model = Sequential([ 
    tf.keras.Input(shape=(28, 28)),  # Updated Input layer syntax
    Flatten(), 
    Dense(128, activation='relu'), 
    Dense(10) 
]) 

# Step 3: Define Loss Function, Optimizer, and Metric
loss_fn = tf.keras.losses.SparseCategoricalCrossentropy(from_logits=True) 
optimizer = tf.keras.optimizers.Adam() 
accuracy_metric = tf.keras.metrics.SparseCategoricalAccuracy() 

# Step 4: Implement the Custom Callback
class CustomCallback(Callback): 
    def on_epoch_end(self, epoch, logs=None): 
        print(f'End of epoch {epoch + 1}, loss: {logs.get("loss")}, accuracy: {logs.get("accuracy")}') 

# Step 5: Implement the Custom Training Loop with Custom Callback
custom_callback = CustomCallback() 

for epoch in range(5): 
    for x_batch, y_batch in train_dataset: 
        with tf.GradientTape() as tape: 
            logits = model(x_batch, training=True) 
            loss = loss_fn(y_batch, logits) 
        grads = tape.gradient(loss, model.trainable_weights) 
        optimizer.apply_gradients(zip(grads, model.trainable_weights)) 
        accuracy_metric.update_state(y_batch, logits) 
    custom_callback.on_epoch_end(epoch, logs={'loss': loss.numpy(), 'accuracy': accuracy_metric.result().numpy()}) 
    accuracy_metric.reset_state()  # Updated method



### Exercise 4: Lab - Hyperparameter Tuning 

#### Enhancement: Add functionality to save the results of each hyperparameter tuning iteration as JSON files in a specified directory. 

#### Additional Instructions:

Modify the tuning loop to save each iteration's results as JSON files.

Specify the directory where these JSON files will be stored for easier retrieval and analysis of tuning results.


In [39]:
# Write your code here
import json
import os
import keras_tuner as kt
from tensorflow.keras import Sequential
from tensorflow.keras.layers import Dense
from tensorflow.keras.optimizers import Adam
from sklearn.model_selection import train_test_split
from sklearn.datasets import make_classification

# Step 1: Load your dataset
X, y = make_classification(n_samples=1000, n_features=20, n_classes=2)
X_train, X_val, y_train, y_val = train_test_split(X, y, test_size=0.2)

# Step 2: Define the model-building function
def build_model(hp):
    model = Sequential()
    # Tune the number of units in the first Dense layer
    model.add(Dense(units=hp.Int('units', min_value=32, max_value=512, step=32),
                    activation='relu'))
    model.add(Dense(1, activation='sigmoid'))  # Binary classification example
    model.compile(optimizer=Adam(hp.Float('learning_rate', 1e-4, 1e-2, sampling='LOG')),
                  loss='binary_crossentropy',
                  metrics=['accuracy'])
    return model

# Step 3: Initialize a Keras Tuner RandomSearch tuner
tuner = kt.RandomSearch(
    build_model,
    objective='val_accuracy',
    max_trials=10,  # Set the number of trials
    executions_per_trial=1,  # Set how many executions per trial
    directory='tuner_results',  # Directory for saving logs
    project_name='hyperparam_tuning'
)

# Step 4: Run the tuner search (make sure the data is correct)
tuner.search(X_train, y_train, validation_data=(X_val, y_val), epochs=5)

# Step 5: Save the tuning results as JSON files
try:
    for i in range(10):
        # Fetch the best hyperparameters from the tuner
        best_hps = tuner.get_best_hyperparameters(num_trials=1)[0]
        
        # Results dictionary to save hyperparameters and score
        results = {
            "trial": i + 1,
            "hyperparameters": best_hps.values,  # Hyperparameters tuned in this trial
            "score": None  # Add any score or metrics if available
        }

        # Save the results as JSON
        with open(os.path.join('tuner_results/hyperparam_tuning', f"trial_{i + 1}.json"), "w") as f:
            json.dump(results, f)

except IndexError:
    print("Tuning process has not completed or no results available.")

Reloading Tuner from tuner_results/hyperparam_tuning/tuner0.json


<details>
<summary>Click here for solution</summary> </br>

```python
!pip install keras-tuner
!pip install scikit-learn

import json
import os
import keras_tuner as kt
from tensorflow.keras import Sequential
from tensorflow.keras.layers import Dense
from tensorflow.keras.optimizers import Adam
from sklearn.model_selection import train_test_split
from sklearn.datasets import make_classification

# Step 1: Load your dataset
X, y = make_classification(n_samples=1000, n_features=20, n_classes=2)
X_train, X_val, y_train, y_val = train_test_split(X, y, test_size=0.2)

# Step 2: Define the model-building function
def build_model(hp):
    model = Sequential()
    # Tune the number of units in the first Dense layer
    model.add(Dense(units=hp.Int('units', min_value=32, max_value=512, step=32),
                    activation='relu'))
    model.add(Dense(1, activation='sigmoid'))  # Binary classification example
    model.compile(optimizer=Adam(hp.Float('learning_rate', 1e-4, 1e-2, sampling='LOG')),
                  loss='binary_crossentropy',
                  metrics=['accuracy'])
    return model

# Step 3: Initialize a Keras Tuner RandomSearch tuner
tuner = kt.RandomSearch(
    build_model,
    objective='val_accuracy',
    max_trials=10,  # Set the number of trials
    executions_per_trial=1,  # Set how many executions per trial
    directory='tuner_results',  # Directory for saving logs
    project_name='hyperparam_tuning'
)

# Step 4: Run the tuner search (make sure the data is correct)
tuner.search(X_train, y_train, validation_data=(X_val, y_val), epochs=5)

# Step 5: Save the tuning results as JSON files
try:
    for i in range(10):
        # Fetch the best hyperparameters from the tuner
        best_hps = tuner.get_best_hyperparameters(num_trials=1)[0]
        
        # Results dictionary to save hyperparameters and score
        results = {
            "trial": i + 1,
            "hyperparameters": best_hps.values,  # Hyperparameters tuned in this trial
            "score": None  # Add any score or metrics if available
        }

        # Save the results as JSON
        with open(os.path.join('tuning_results', f"trial_{i + 1}.json"), "w") as f:
            json.dump(results, f)

except IndexError:
    print("Tuning process has not completed or no results available.")
 ```   

</details>


### Exercise 5: Explanation of Hyperparameter Tuning

**Addition to Explanation:** Add a note explaining the purpose of num_trials in the hyperparameter tuning context:


In [40]:
# Write your code here
## num_trials specifies the number of top hyperparameter sets to return. num_trials=1 means it will return only the bestest set of hyperparameters found during the hypertuning process.

<details>
<summary>Click here for solution</summary> </br>

```python
Explanation: "num_trials specifies the number of top hyperparameter sets to return. Setting num_trials=1 means that it will return only the best set of hyperparameters found during the tuning process."
 ```   

</details>


### Conclusion: 

Congratulations on completing this lab! You have now successfully created, trained, and evaluated a simple neural network model using the Keras Functional API. This foundational knowledge will allow you to build more complex models and explore advanced functionalities in Keras. 


Copyright © IBM Corporation. All rights reserved.
